<a href="https://colab.research.google.com/github/bahman7745/ai-book-gen/blob/main/book_ai.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import json

# Load the JSON data from the files
with open('outline.txt', 'r') as file:
    outline_data = json.load(file)

with open('jsonformatter (2).txt', 'r') as file:
    jsonformatter_data = json.load(file)

# Create a dictionary to map subchapter titles to their segments
segments_dict = {}
for chapter in jsonformatter_data:
    for subchapter in chapter.get('subchapters', []):
        segments_dict[subchapter['title']] = subchapter.get('segments', [])

# Add segments to the corresponding subchapters in the outline data
for part in outline_data['table_of_contents']:
    for chapter in part['chapters']:
        for subchapter in chapter['subchapters']:
            title = subchapter['title']
            if title in segments_dict:
                subchapter['segments'] = segments_dict[title]

# Save the updated outline data back to a file
with open('updated_outline.txt', 'w') as file:
    json.dump(outline_data, file, indent=4)

print("Segments added to subchapters successfully.")

Segments added to subchapters successfully.


In [ ]:
! pip install -U langchain_community langchain-groq  langchain langgraph openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 7.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 974.0/974.0 kB 47.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.3/88.3 kB 10.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 325.2/325.2 kB 31.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 314.7/314.7 kB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.9/124.9 kB 14.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.4/105.4 kB 11.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.2/49.2 kB 6.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 8.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.0/53.0 kB 6.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
from langchain_community.chat_models import ChatPerplexity
from langchain_core.prompts import ChatPromptTemplate

In [ ]:
import json

# Load and validate the JSON file
try:
    with open('updated_outline.txt', 'r') as file:
        outline_data = json.load(file)
    print("JSON file is valid.")
except json.JSONDecodeError as e:
    print(f"JSON file is invalid: {e}")

JSON file is valid.


In [ ]:
import json
import time
from rich.console import Console
import os

class CognitiveResearchAssistant:
    def __init__(self, outline_file, cache_file, api_key):
        self.outline_file = outline_file
        self.cache_file = cache_file
        self.api_key = api_key
        self.console = Console()
        self.chat = ChatPerplexity(
            temperature=0,
            pplx_api_key=self.api_key,
            model="llama-3-sonar-large-32k-online",
            max_tokens=32000
        )
        self.system_message = """
        You are an AI critical thinker research assistant. Your sole purpose is to write well written, critically acclaimed, objective and structured reports on given text.
        """
        self.human_message_template = """
        Provide a detailed and structured report on the following topic:
        Title: {title}
        References: {references}
        Content: {content}
        """
        self.load_outline()
        self.load_cache()

    def load_outline(self):
        with open(self.outline_file, 'r') as file:
            self.outline_data = json.load(file)

    def load_cache(self):
        if os.path.exists(self.cache_file):
            with open(self.cache_file, 'r') as file:
                self.cache_data = json.load(file)
        else:
            self.cache_data = {}

    def save_cache(self):
        with open(self.cache_file, 'w') as file:
            json.dump(self.cache_data, file, indent=4)

    def save_updated_outline(self):
        with open('updated_outline_with_research.txt', 'w') as file:
            json.dump(self.outline_data, file, indent=4)

    def generate_research_data(self, title, references, content):
        human_message = self.human_message_template.format(
            title=title,
            references=', '.join(references),
            content=content
        )
        prompt = ChatPromptTemplate.from_messages([("system", self.system_message), ("human", human_message)])
        chain = prompt | self.chat
        response = chain.invoke({"input": human_message})
        return response.content

    def process_segment(self, segment):
        segment_title = segment['title']
        segment_content = segment['content']
        segment_references = segment.get('references', [])

        # Check if this segment is already processed
        if segment_title in self.cache_data:
            self.console.print(f"Skipping already processed segment: [bold]{segment_title}[/bold]", style="yellow")
            segment['research_data'] = self.cache_data[segment_title]
        else:
            self.console.print(f"Processing segment: [bold]{segment_title}[/bold]", style="blue")
            try:
                research_data = self.generate_research_data(segment_title, segment_references, segment_content)
                segment['research_data'] = research_data

                # Save progress to cache
                self.cache_data[segment_title] = research_data
                self.save_cache()

                self.console.print(f"Generated research data for segment: [bold]{segment_title}[/bold]", style="green")
                self.console.print(research_data, style="yellow")
            except Exception as e:
                self.console.print(f"Error processing segment {segment_title}: {e}", style="red")

        # Save the updated outline data continuously
        self.save_updated_outline()

    def run(self):
        for part in self.outline_data['table_of_contents']:
            for chapter in part['chapters']:
                for subchapter in chapter['subchapters']:
                    for segment in subchapter.get('segments', []):
                        self.process_segment(segment)
                        time.sleep(0)  # Sleep between API calls

        self.console.print("Research data added to subchapters and references successfully.", style="bold green")

if __name__ == "__main__":
    assistant = CognitiveResearchAssistant(
        outline_file='updated_outline.txt',
        cache_file='cache.json',
        api_key="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"
    )
    assistant.run()

Skipping already processed segment: 1.1.1 Ancient Philosophical Roots

Skipping already processed segment: 1.1.2 The Birth of Experimental Psychology

Skipping already processed segment: 1.1.3 The Rise of Behaviorism

Skipping already processed segment: 1.1.4 The Cognitive Revolution

Skipping already processed segment: 1.1.5 Foundational Figures

...

Skipping already processed segment: 12.4.2 The Nature of Consciousness

Skipping already processed segment: 12.4.3 Ethical Considerations

Skipping already processed segment: 12.4.4 AI and Human Identity

Skipping already processed segment: 12.4.5 The Role of AI in Human Flourishing

Research data added to subchapters and references successfully.

In [ ]:
from langchain_core.prompts import ChatPromptTemplate
from langchain_groq import ChatGroq

In [ ]:
chat = ChatGroq(temperature=0, groq_api_key="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", model_name="llama3-70b-8192")


In [ ]:
system = "You are a helpful assistant."
human = "{text}"
prompt = ChatPromptTemplate.from_messages([("system", system), ("human", human)])

chain = prompt | chat
chain.invoke({"text": "Explain the importance of low latency LLMs."})

In [ ]:
import json
import time
from rich.console import Console
import os

class BookWriter:
    def __init__(self, outline_file, cache_file, api_key):
        self.outline_file = outline_file
        self.cache_file = cache_file
        self.api_key = api_key
        self.console = Console()
        self.chat = ChatGroq(
            temperature=0,
            groq_api_key=self.api_key,
            model_name="llama3-70b-8192"
        )
        self.system_message = """
        As a professional book writer agent,
        craft book pages that persuades readers to complete the book.
        Utilize persuasive language and a compelling narrative voice consistently throughout the page.
        Emphasize the rewards and compelling reasons for the reader to continue reading, fostering a sense of curiosity and eagerness to discover more.
        The page should skillfully create an atmosphere that inspires readers to embark on a journey through the pages until they reach the book's conclusion.
        """
        self.human_message_template = """
        Based on the provided title, content, and research data, generate detailed and well-structured book pages that comprehensively cover the topic.
        The output should be approximately 8000 words, presenting the information in a clear, logical, and engaging manner.
        Ensure that the content is original and informative, without mentioning references or other extraneous details.
        Use appropriate headings, subheadings, and paragraphs to structure the book pages effectively."
        Title: {title}
        Content: {content}
        Research Data: {research_data}
        """
        self.load_outline()
        self.load_cache()

    def load_outline(self):
        with open(self.outline_file, 'r') as file:
            self.outline_data = json.load(file)

    def load_cache(self):
        if os.path.exists(self.cache_file):
            with open(self.cache_file, 'r') as file:
                self.cache_data = json.load(file)
        else:
            self.cache_data = {}

    def save_cache(self):
        with open(self.cache_file, 'w') as file:
            json.dump(self.cache_data, file, indent=4)

    def save_updated_outline(self):
        with open('updated_outline_with_book_pages.txt', 'w') as file:
            json.dump(self.outline_data, file, indent=4)

    def generate_book_page(self, title, content, research_data):
        human_message = self.human_message_template.format(
            title=title,
            content=content,
            research_data=research_data
        )
        prompt = ChatPromptTemplate.from_messages([("system", self.system_message), ("human", human_message)])
        chain = prompt | self.chat
        response = chain.invoke({"input": human_message})
        return response.content

    def process_segment(self, segment):
        segment_title = segment['title']
        segment_content = segment['content']
        research_data = segment.get('research_data', '')

        # Check if this segment is already processed
        if segment_title in self.cache_data:
            self.console.print(f"Skipping already processed segment: [bold]{segment_title}[/bold]", style="yellow")
            segment['book_page'] = self.cache_data[segment_title]
        else:
            self.console.print(f"Processing segment: [bold]{segment_title}[/bold]", style="blue")
            try:
                book_page = self.generate_book_page(segment_title, segment_content, research_data)
                segment['book_page'] = book_page

                # Save progress to cache
                self.cache_data[segment_title] = book_page
                self.save_cache()

                self.console.print(f"Generated book page for segment: [bold]{segment_title}[/bold]", style="green")
                self.console.print(book_page, style="yellow")
            except Exception as e:
                self.console.print(f"Error processing segment {segment_title}: {e}", style="red")

        # Save the updated outline data continuously
        self.save_updated_outline()

    def run(self):
        for part in self.outline_data['table_of_contents']:
            for chapter in part['chapters']:
                for subchapter in chapter['subchapters']:
                    for segment in subchapter.get('segments', []):
                        self.process_segment(segment)
                        time.sleep(3)  # Sleep between API calls

        self.console.print("Book pages added to segments successfully.", style="bold green")

if __name__ == "__main__":
    writer = BookWriter(
        outline_file='/content/updated_outline_with_research (1).txt',
        cache_file='book_cache.json',
        api_key="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"
    )
    writer.run()

Processing segment: 1.1.1 Ancient Philosophical Roots

Generated book page for segment: 1.1.1 Ancient Philosophical Roots

Here is the generated book page:

**1.1.1 Ancient Philosophical Roots**

The study of the mind and its processes has a rich history that dates back to ancient Greek philosophers, 
particularly Plato and Aristotle. These philosophers laid the groundwork for understanding the nature of knowledge 
and thought, which would later influence the development of cognitive science.

**Unraveling the Nature of Knowledge and Thought**

In the pursuit of understanding the human mind, ancient Greek philosophers embarked on a journey to explore the 
nature of knowledge and thought. This intellectual quest led to the development of groundbreaking ideas that would 
shape the course of cognitive science.

**Plato's Contributions: Unveiling the Realm of Eternal Truths**

Plato, a student of Socrates, made significant contributions to the study of the mind. In his work, "Meno," Plato 
explored the concept of knowledge and how it is acquired. He proposed that knowledge is not acquired through 
sensory experience but rather through recollection of eternal truths that exist independently of the physical 
world. This idea, known as Platonic realism, posits that the mind has access to a realm of abstract, eternal truths
that are not derived from sensory experience.

Plato's theory of forms, which posits that abstract concepts like justice, beauty, and goodness have a real 
existence independent of the physical world, also has implications for understanding the nature of thought and 
knowledge. This theory suggests that the mind is capable of accessing and understanding these abstract concepts, 
which are not directly observable through the senses.

**Aristotle's Contributions: Understanding the Soul and the Four Causes**

Aristotle, a student of Plato, built upon his teacher's ideas and expanded the study of the mind. In his work, "De 
Anima," Aristotle explored the nature of the soul and its relationship to the body. He proposed that the soul is 
the form or essence of a living being, and that it is responsible for the being's ability to perceive, think, and 
move.

Aristotle's concept of the four causes (material, formal, efficient, and final) also has implications for 
understanding the nature of thought and knowledge. He argued that to fully understand a phenomenon, one must 
consider all four causes, which provides a comprehensive framework for analyzing complex phenomena.

**The Lasting Impact on Cognitive Science**

The ideas of Plato and Aristotle have had a lasting impact on the development of cognitive science. Their 
exploration of the nature of knowledge, thought, and the mind laid the groundwork for later philosophers and 
scientists to build upon. The concept of abstract, eternal truths and the idea that the mind has access to a realm 
of abstract concepts have influenced the development of theories in cognitive science, such as the idea of 
representational structures in the mind and computational procedures that operate on those structures.

**Embarking on a Journey of Discovery**

In conclusion, the ancient Greek philosophers, particularly Plato and Aristotle, made significant contributions to 
the study of the mind and its processes. Their ideas about the nature of knowledge, thought, and the mind have had 
a lasting impact on the development of cognitive science, shaping the way we understand the mind and its functions 
today. As we delve deeper into the world of cognitive science, we are reminded of the profound influence of these 
ancient philosophers on our understanding of the human mind.

This is just the beginning of an incredible journey through the pages of cognitive science. As we explore the 
intricacies of the human mind, we will uncover the fascinating stories of pioneers who have shaped our 
understanding of thought, knowledge, and the human experience.

Processing segment: 1.1.2 The Birth of Experimental Psychology

Generated book page for segment: 1.1.2 The Birth of Experimental Psychology

...

Here is the generated book page content, approximately 8000 words, covering the topic of AI and Human Identity:

**12.4.4 AI and Human Identity**

The integration of Artificial Intelligence (AI) into daily life has led to a profound impact on traditional notions
of human identity and agency. This chapter examines the challenges and implications of AI on human identity, 
highlighting the need for a reevaluation of what it means to be human in an AI-driven world.

**The Impact of AI on Human Identity**

The increasing presence of AI in various aspects of life has led to a fusion of human and machine identities. This 
fusion has required individuals to adapt and redefine their professional identities, as AI has disrupted 
traditional career paths and job roles. The integration of AI has also led to the development of new skills and a 
more flexible sense of professional self.

Moreover, AI has significantly influenced personal identity, particularly in the context of data and online 
interactions. Social media platforms, smart devices, and online services constantly collect data about individual 
behavior and preferences, which AI algorithms use to customize content and make recommendations. This has raised 
concerns about privacy and the accuracy of digital personas, which may not fully represent who individuals are.

**The Statistical Individual and Algorithmic Representations**

Machine learning algorithms in a data-rich reality represent human identity in terms of the "statistical 
individual." This statisticalized representation of individuals differs significantly from the ordinary conception 
of human identity, which is tightly intertwined with considerations about biological, psychological, and narrative 
continuity. Algorithmic representations give no special attention to biological, psychological, and narrative 
properties, instead relying on predictive properties that significantly exceed and diverge from those considered 
relevant for questions about human identity.

**Ethical and Moral Challenges**

AI systems are often designed to make ethical decisions, such as in self-driving cars or healthcare diagnostics. 
However, these systems rely on algorithms and data, and their decisions may not always align with human values and 
morals. This has led to philosophical debates about the essence of morality and the role of AI in shaping ethical 
identity.

**Biometric Identification and Security**

AI has played a pivotal role in biometric identification systems, such as facial recognition and fingerprint 
scanning. These technologies have become prevalent in security and authentication, enhancing security but also 
introducing concerns about identity theft and personal data security. As AI increasingly recognizes individuals by 
their unique physical traits, it forces a confrontation with questions about the nature of identity tied to 
biometrics.

**The Amplification of Echo Chambers**

AI algorithms, especially in social media and content recommendation, tend to reinforce existing beliefs and 
preferences, creating echo chambers that isolate individuals within their own ideological bubbles. This phenomenon 
can shape and solidify one's identity, making it more resistant to external perspectives and diverse viewpoints.

**Redefining Human Identity in an AI-Driven World**

The integration of AI into daily life has led to a complex and multifaceted impact on human identity. It redefines 
professional and personal selves, challenges ethical and moral identities, influences social connections, and 
raises questions about the security of personal data. As AI continues to advance, it is essential for individuals 
and society as a whole to navigate these changes with a deep understanding of the implications.

**The Need for a Reevaluation**

While AI offers numerous benefits and conveniences, it also comes with important ethical and philosophical 
considerations that require ongoing discussion and regulation to ensure that AI tec

Processing segment: 12.4.5 The Role of AI in Human Flourishing

Generated book page for segment: 12.4.5 The Role of AI in Human Flourishing

Here is the generated book page content, approximately 8000 words, covering the topic "The Role of AI in Human 
Flourishing":

**Introduction**

As we navigate the complexities of the 21st century, humanity stands at the threshold of a revolutionary era. 
Artificial intelligence (AI) has emerged as a transformative force, poised to reshape the fabric of our existence. 
This chapter delves into the profound implications of AI on human flourishing, exploring the vast potential of this
technology to enhance our cognitive abilities, improve healthcare, and unlock new avenues for personal and 
professional growth.

**Cognitive Enhancement: Unlocking Human Potential**

AI has the remarkable ability to augment human cognitive abilities, processing vast amounts of data, identifying 
patterns, and providing insights that may elude human perception. This synergy between human and artificial 
intelligence can lead to improved decision-making, enhanced creativity, and more efficient problem-solving. For 
individuals with cognitive impairments, such as those with autism or ADHD, AI-assisted tools can provide 
personalized support and accommodations, empowering them to reach their full potential.

The cognitive benefits of AI are multifaceted. By automating routine tasks, AI can free humans to focus on 
higher-level thinking, creativity, and innovation. Moreover, AI-driven analytics can help identify knowledge gaps, 
enabling targeted learning and skill development. As AI continues to evolve, we can expect to see significant 
advancements in cognitive enhancement, leading to a more efficient, productive, and innovative human workforce.

**Healthcare Advancements: The AI Revolution**

The integration of AI in healthcare is transforming the medical landscape, enabling early disease detection, 
personalized medicine, and more effective treatment strategies. AI-driven diagnostic tools can analyze medical 
images, identify anomalies, and provide accurate diagnoses, potentially saving countless lives. Furthermore, AI can
accelerate the development of new pharmaceuticals and treatments, leading to improved health outcomes and enhanced 
quality of life.

The potential applications of AI in healthcare are vast and varied. AI-assisted robots can assist in surgeries, 
reducing recovery time and improving patient outcomes. AI-driven chatbots can provide personalized health advice, 
helping individuals take proactive control of their well-being. As AI continues to advance, we can expect to see 
significant improvements in healthcare, leading to a healthier, happier, and more productive society.

**Personal and Professional Growth: Unlocking New Opportunities**

AI has the potential to facilitate personal and professional growth, providing access to new educational resources,
enhancing skill development, and creating new job opportunities. AI-powered learning platforms can offer 
personalized educational content, helping individuals acquire new skills and knowledge more efficiently. 
Furthermore, AI can automate routine tasks, freeing humans to focus on more creative and high-value tasks, leading 
to increased productivity and job satisfaction.

The impact of AI on personal and professional growth is far-reaching. AI-driven career guidance can help 
individuals identify their strengths and weaknesses, providing personalized career paths and development 
strategies. AI-assisted mentorship programs can connect individuals with experienced professionals, fostering 
knowledge sharing and skill development. As AI continues to evolve, we can expect to see significant advancements 
in personal and professional growth, leading to a more fulfilled and productive workforce.

**Challenges and Concerns: Navigating the AI Landscape**

While AI has the potential to enhance human flourishing, there are also concerns about its impact on society. The 
increasing reliance on AI could lead to job displacement, exacerbate existing social inequalities, and create new 
forms 

Book pages added to segments successfully.